Hello, my name is Aaron Kann.  In this data analysis, I seek to determine the point in the season in which a player's year to date averages become a better predictor of future outputs than a players previous year averages.

I expect that, in the first couple of weeks into a Premier League Season, a player's previous averages are a stronger predictive metric because a player's to date averages are suggested to a much greater degree of variance.  However, I hypothesize that around matchweek 6, a player's to date averages become a stronger metric because the recency advantage outweighs the larger variance.  

In addition, I expect that for metrics with a lower total count (goals, assists, yellow cards, etc.), last years output may be a more relevant factor for longer than metrics with a greater total count (total passes, shots attempted, clearances etc), because the high variance is magnified in these cases. 

Let's see if the data supports my hypotheses!

In [1]:
import csv, os, sys
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import statsmodels.api as sm

# Read the data from the csv file
if not 'Premier_League_Team_Stats.csv' in os.listdir():
    os.chdir('..')
import fbref_scrape as fbref
from constants import *


In [2]:
def add_name_to_df(df, file):
    name = file.split('Matchlogs')[0]
    # get rid of the last underscore, and change all other underscores to spaces
    name = name[:-1].replace('_', ' ')
    # add the name all rows in the dataframe
    df['Name'] = name
    return df

In [3]:
prev_yr_df = pd.read_csv('Premier_League_Player_Stats.csv')

data_folder = 'Premier_League_Player_Matchlogs'
data_files = os.listdir(data_folder)
dfs = []
dfs_names = []

for file in data_files:
    if file.endswith('.csv'):
        file_path = os.path.join(data_folder, file)
        # read the csv file and process the data
        df = pd.read_csv(file_path)
        df = add_name_to_df(df, file)
        dfs.append(df)
        dfs_names.append(file)

dfs[0].head()

game_started  game_count dayofweek            comp        round venue  \
0            Y           1       Mon  Premier League  Matchweek 1  Home   
1            Y           2       Sat  Premier League  Matchweek 2  Away   
2            Y           3       Sat  Premier League  Matchweek 3  Home   
3            Y           4       Sun  Premier League  Matchweek 4  Away   
4            N           5       Sat  Premier League  Matchweek 5  Home   

  result            team         opponent position  ...  passes_completed  \
0  W 1-0  Manchester Utd           Wolves       RB  ...                47   
1  L 0-2  Manchester Utd        Tottenham       RB  ...                38   
2  W 3-2  Manchester Utd  Nott'ham Forest       RB  ...                58   
3  L 1-3  Manchester Utd          Arsenal       RB  ...                44   
4  L 1-3  Manchester Utd         Brighton       CB  ...                10   

   passes  passes_pct  progressive_passes  carries  progressive_carries  \
0      51        92.2                   3       42                    1   
1      44        86.4                   1       29                    1   
2      69        84.1                   9       55                    7   
3      54        81.5                   2       30                    2   
4      11        90.9                   1        5                    0   

   take_ons  take_ons_won  match_report               Name  
0         4             3  Match Report  Aaron Wan Bissaka  
1         2             1  Match Report  Aaron Wan Bissaka  
2         2             1  Match Report  Aaron Wan Bissaka  
3         0             0  Match Report  Aaron Wan Bissaka  
4         0             0  Match Report  Aaron Wan Bissaka  

[5 rows x 38 columns]

In [4]:
def update_avgs(season_avgs, row, index):
    #iterate through the stats in season_avgs and update the averages
    for stat in season_avgs.keys():
        if stat in row.keys():
            if stat == "team":
                continue
            season_avgs[stat] = (season_avgs[stat]*index + row[stat])/(index+1)
    return season_avgs

# Get a player name from the matchlogs file name
def get_player_name(filename):
    return filename.split("_Matchlogs")[0].replace('_', ' ')

def get_player_prev_yr_statline(prev_yr_df, player_name):
    return prev_yr_df[prev_yr_df['name'] == player_name]

In [24]:
stats_wanted = fbref.get_stats_wanted('fbref')
stats_wanted.remove('name')
stats_wanted.remove('team')
stats_wanted.append('game_count')
print(stats_wanted)
df_as_list = list()

for i in range(len(dfs)): #iterates through each player's data
    
    # create a new row, with the season totals as of matchweek 0 (ie all zero)
    season_avgs = pd.Series(data=[0]*len(stats_wanted), index=stats_wanted)
    # print(season_avgs, last_five_avgs)


    for index, row in dfs[i].iterrows(): #iterates through each game of each players data
        # get rid of the buggy goalie statlines, which have no stats TODO: fix this
        if "take_ons_won" not in row.keys():
            continue

        dfrow = pd.concat([row, season_avgs.add_suffix("_szn")], axis=0)
        season_avgs = update_avgs(season_avgs, row, index)

        
        #add last season averages to the list
        dfrow['player_name'] = get_player_name(dfs_names[i])
        prev_yr_statline = get_player_prev_yr_statline(prev_yr_df, dfrow['player_name'])
        
        #iterate through the stats in prev_yr_statline and add them to the row
        if prev_yr_statline.empty:
            continue
        else:
            print(prev_yr_statline)
            for stat in prev_yr_statline.keys():
                print(type(prev_yr_statline))
                print(prev_yr_statline[stat])
                print("type of prev_yr_statline[stat].:")
                print(type(prev_yr_statline[stat]))
                print("----")
                print(type(prev_yr_statline[stat].iloc[0]))
                dfrow[stat + "_prev_yr"] = prev_yr_statline[stat].iloc[0]
            
        #add the row to the list        
        df_as_list.append(dfrow)

    #end game loop
#end player loop

#print the column names of df_as_list
print(df_as_list[0].keys())




df = pd.DataFrame(df_as_list)
df.head()

['games', 'minutes', 'gk_saves', 'clearances', 'tackles', 'assisted_shots', 'fouled', 'shots', 'crosses', 'shots_on_target', 'passes', 'interceptions', 'fouls', 'goals', 'assists', 'cards_yellow', 'game_count']


C:\Users\Aaron\AppData\Local\Temp\ipykernel_9332\3171090442.py:7: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '77.5' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  season_avgs[stat] = (season_avgs[stat]*index + row[stat])/(index+1)
C:\Users\Aaron\AppData\Local\Temp\ipykernel_9332\3171090442.py:7: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '89.5' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  season_avgs[stat] = (season_avgs[stat]*index + row[stat])/(index+1)
C:\Users\Aaron\AppData\Local\Temp\ipykernel_9332\3171090442.py:7: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '46.5' has dtype incompatible with int64, please explicitly cast to a compatible dtype fir

              name  same_team  same_league  gk_saves  games  minutes  goals  \
29  Angelo Ogbonna      False        False         0     16        0      0   

    assists  cards_yellow  passes  assisted_shots  tackles  interceptions  \
29        0             0     415               3       11             17   

    clearances  fouls  fouled  team  crosses  shots  shots_on_target  
29          74      2       4     0        0      3                0  
<class 'pandas.core.frame.DataFrame'>
29    Angelo Ogbonna
Name: name, dtype: object
type of prev_yr_statline[stat].:
<class 'pandas.core.series.Series'>
----
<class 'str'>
<class 'pandas.core.frame.DataFrame'>
29    False
Name: same_team, dtype: bool
type of prev_yr_statline[stat].:
<class 'pandas.core.series.Series'>
----
<class 'numpy.bool_'>
<class 'pandas.core.frame.DataFrame'>
29    False
Name: same_league, dtype: bool
type of prev_yr_statline[stat].:
<class 'pandas.core.series.Series'>
----
<class 'numpy.bool_'>
<class 'pandas.core

C:\Users\Aaron\AppData\Local\Temp\ipykernel_9332\3171090442.py:7: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '16.5' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  season_avgs[stat] = (season_avgs[stat]*index + row[stat])/(index+1)
C:\Users\Aaron\AppData\Local\Temp\ipykernel_9332\3171090442.py:7: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '1.5' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  season_avgs[stat] = (season_avgs[stat]*index + row[stat])/(index+1)
C:\Users\Aaron\AppData\Local\Temp\ipykernel_9332\3171090442.py:7: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '45.5' has dtype incompatible with int64, please explicitly cast to a compatible dtype firs

          name  same_team  same_league  gk_saves  games  minutes  goals  \
13  Ben Davies      False        False         0     31        0      2   

    assists  cards_yellow  passes  assisted_shots  tackles  interceptions  \
13        2             4    1281              20       28             18   

    clearances  fouls  fouled  team  crosses  shots  shots_on_target  
13          72     30      17     0        0     14                0  
<class 'pandas.core.frame.DataFrame'>
13    Ben Davies
Name: name, dtype: object
type of prev_yr_statline[stat].:
<class 'pandas.core.series.Series'>
----
<class 'str'>
<class 'pandas.core.frame.DataFrame'>
13    False
Name: same_team, dtype: bool
type of prev_yr_statline[stat].:
<class 'pandas.core.series.Series'>
----
<class 'numpy.bool_'>
<class 'pandas.core.frame.DataFrame'>
13    False
Name: same_league, dtype: bool
type of prev_yr_statline[stat].:
<class 'pandas.core.series.Series'>
----
<class 'numpy.bool_'>
<class 'pandas.core.frame.DataF

...

C:\Users\Aaron\AppData\Local\Temp\ipykernel_9332\3171090442.py:7: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '1.5' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  season_avgs[stat] = (season_avgs[stat]*index + row[stat])/(index+1)
C:\Users\Aaron\AppData\Local\Temp\ipykernel_9332\3171090442.py:7: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '2.5' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  season_avgs[stat] = (season_avgs[stat]*index + row[stat])/(index+1)
C:\Users\Aaron\AppData\Local\Temp\ipykernel_9332\3171090442.py:7: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '0.5' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.

               name  same_team  same_league  gk_saves  games  minutes  goals  \
15  Vladimir Coufal      False        False         0     27        0      0   

    assists  cards_yellow  passes  assisted_shots  tackles  interceptions  \
15        1             5    1174              26       58             38   

    clearances  fouls  fouled  team  crosses  shots  shots_on_target  
15          70     30      21     0        0      6                0  
<class 'pandas.core.frame.DataFrame'>
15    Vladimir Coufal
Name: name, dtype: object
type of prev_yr_statline[stat].:
<class 'pandas.core.series.Series'>
----
<class 'str'>
<class 'pandas.core.frame.DataFrame'>
15    False
Name: same_team, dtype: bool
type of prev_yr_statline[stat].:
<class 'pandas.core.series.Series'>
----
<class 'numpy.bool_'>
<class 'pandas.core.frame.DataFrame'>
15    False
Name: same_league, dtype: bool
type of prev_yr_statline[stat].:
<class 'pandas.core.series.Series'>
----
<class 'numpy.bool_'>
<class 'pandas.c

C:\Users\Aaron\AppData\Local\Temp\ipykernel_9332\3171090442.py:7: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '42.5' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  season_avgs[stat] = (season_avgs[stat]*index + row[stat])/(index+1)
C:\Users\Aaron\AppData\Local\Temp\ipykernel_9332\3171090442.py:7: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '0.5' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  season_avgs[stat] = (season_avgs[stat]*index + row[stat])/(index+1)
C:\Users\Aaron\AppData\Local\Temp\ipykernel_9332\3171090442.py:7: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '0.5' has dtype incompatible with int64, please explicitly cast to a compatible dtype first

            name  same_team  same_league  gk_saves  games  minutes  goals  \
9  Yves Bissouma      False        False         0     23        0      0   

   assists  cards_yellow  passes  assisted_shots  tackles  interceptions  \
9        0             6     733               8       16             12   

   clearances  fouls  fouled  team  crosses  shots  shots_on_target  
9          10     17      10     0        0      6                0  
<class 'pandas.core.frame.DataFrame'>
9    Yves Bissouma
Name: name, dtype: object
type of prev_yr_statline[stat].:
<class 'pandas.core.series.Series'>
----
<class 'str'>
<class 'pandas.core.frame.DataFrame'>
9    False
Name: same_team, dtype: bool
type of prev_yr_statline[stat].:
<class 'pandas.core.series.Series'>
----
<class 'numpy.bool_'>
<class 'pandas.core.frame.DataFrame'>
9    False
Name: same_league, dtype: bool
type of prev_yr_statline[stat].:
<class 'pandas.core.series.Series'>
----
<class 'numpy.bool_'>
<class 'pandas.core.frame.DataF

game_started  game_count dayofweek            comp         round venue  \
0            N           1       Sun  Premier League   Matchweek 2  Home   
1            Y           2       Sat  Premier League   Matchweek 3  Away   
2            N           3       Sun  Premier League  Matchweek 12  Home   
3            N           4       Sun  Premier League  Matchweek 16  Away   
4            Y           5       Thu  Premier League  Matchweek 19  Away   

  result      team         opponent position  ...  assisted_shots_prev_yr  \
0  W 3-1  West Ham          Chelsea       CB  ...                       3   
1  W 3-1  West Ham         Brighton       CB  ...                       3   
2  W 3-2  West Ham  Nott'ham Forest       RW  ...                       3   
3  L 0-5  West Ham           Fulham       CB  ...                       3   
4  W 2-0  West Ham          Arsenal       CB  ...                       3   

   tackles_prev_yr  interceptions_prev_yr  clearances_prev_yr  fouls_prev_yr  \
0               11                     17                  74              2   
1               11                     17                  74              2   
2               11                     17                  74              2   
3               11                     17                  74              2   
4               11                     17                  74              2   

   fouled_prev_yr  team_prev_yr  crosses_prev_yr  shots_prev_yr  \
0               4             0                0              3   
1               4             0                0              3   
2               4             0                0              3   
3               4             0                0              3   
4               4             0                0              3   

   shots_on_target_prev_yr  
0                        0  
1                        0  
2                        0  
3                        0  
4                        0  

[5 rows x 76 columns]

In [25]:
for obj in df_as_list:
    if not (len(obj.keys()) == len(df_as_list[0].keys())):
        print(obj.keys())
        print(df_as_list[0].keys())
        print(len(obj.keys()))
        print(len(df_as_list[0].keys()))

df.to_csv('prev_yr_output.csv', index=False)

In [37]:
# Iterate though each of the matchweeks, performing a linear regression on the data
for i in range(38):
    if i in [0, 1]:
        continue
    # Get the data for the current matchweek
    matchweek_data = df[df['game_count'] == i]
    print(matchweek_data.shape)
    # Perform a linear regression on the data
    # Get the x and y values
    Y = np.array(matchweek_data['passes'])
    X = np.array(matchweek_data[['passes_prev_yr', 'passes_szn']])
    X = sm.add_constant(X)

    model = sm.OLS(Y, X).fit()
    
    # standardized_coefficients = model.params / np.std(X, axis=0)

    # # Find the index of the predictor with the highest absolute standardized coefficient
    # better_predictor_index = np.argmax(np.abs(standardized_coefficients))
    # print(bette)

    # # Map the index back to the corresponding column name
    # column_names = ['passes_prev_yr', 'passes_szn']
    # better_predictor = column_names[better_predictor_index]

    # print(better_predictor)
    
    if (i in [2, 4, 6, 11, 19, 28]):
        print(model.summary())

(41, 76)
                            OLS Regression Results                            
Dep. Variable:                      y   R-squared:                       0.214
Model:                            OLS   Adj. R-squared:                  0.172
Method:                 Least Squares   F-statistic:                     5.160
Date:                Mon, 12 Aug 2024   Prob (F-statistic):             0.0104
Time:                        12:31:10   Log-Likelihood:                -171.87
No. Observations:                  41   AIC:                             349.7
Df Residuals:                      38   BIC:                             354.9
Df Model:                           2                                         
Covariance Type:            nonrobust                                         
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
const         13.2740      5.687      2.334